In [2]:
import os

os.environ["TAVILY_API_KEY"] = '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'
os.environ["LANGCHAIN_ENDPOINT"] = "https://api.smith.langchain.com"
os.environ["LANGCHAIN_TRACING_V2"] = "true"
os.environ["LANGCHAIN_API_KEY"] = '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'
os.environ["HTTP_PROXY"] = '192.168.208.104:7890'
os.environ["HTTPS_PROXY"] = '192.168.208.104:7890'

In [3]:
from langchain_community.embeddings import HuggingFaceEmbeddings

hf = HuggingFaceEmbeddings(model_name="BAAI/bge-base-en", model_kwargs={"device": "cpu"})
os.environ['HTTP_PROXY'] = ''
os.environ['HTTPS_PROXY'] = ''

/home/zhuxy/anaconda3/envs/OSAF/lib/python3.9/site-packages/langchain_core/_api/deprecation.py:119: LangChainDeprecationWarning: The class `HuggingFaceEmbeddings` was deprecated in LangChain 0.2.2 and will be removed in 0.3.0. An updated version of the class exists in the langchain-huggingface package and should be used instead. To use it run `pip install -U langchain-huggingface` and import as `from langchain_huggingface import HuggingFaceEmbeddings`.
  warn_deprecated(
/home/zhuxy/anaconda3/envs/OSAF/lib/python3.9/site-packages/sentence_transformers/cross_encoder/CrossEncoder.py:11: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from tqdm.autonotebook import tqdm, trange
/home/zhuxy/anaconda3/envs/OSAF/lib/python3.9/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If

In [4]:
import os
from neo4j import GraphDatabase

# 从环境变量加载Neo4j连接信息
NEO4J_URI = os.getenv("NEO4J_URI", "bolt://localhost:7687")
NEO4J_USERNAME = os.getenv("NEO4J_USERNAME", "neo4j")
NEO4J_PASSWORD = os.getenv("NEO4J_PASSWORD", "neo4jneo4j")

# 创建Neo4j驱动
driver = GraphDatabase.driver(NEO4J_URI, auth=(NEO4J_USERNAME, NEO4J_PASSWORD))

# 定义查询语句，获取与seL4节点通过SPECIFY关系直接连接的所有节点
query = """
MATCH (seL4 {name: "seL4"})-[:SPECIFY]->(relatedNode)
RETURN relatedNode.name AS name
"""

# 执行查询并获取结果
def get_specify_related_nodes(tx):
    result = tx.run(query)
    return [record["name"] for record in result]

with driver.session() as session:
    related_nodes = session.read_transaction(get_specify_related_nodes)
    print("Nodes directly connected to seL4 through SPECIFY:", related_nodes)

# 关闭驱动
driver.close()

Nodes directly connected to seL4 through SPECIFY: ['System Calls', 'An Initial Kernel State', 'Decoding System Calls', 'Kernel Invocation Labels', 'Interrupts', 'IPC', 'Threads and TCBs', 'Scheduler', 'Toplevel ARM Definitions', 'CSpace', 'Prefix order on lists as order class instance', 'IPC Cancelling', 'ARM VSpace Functions', 'Retyping and Untyped Invocations', 'Kernel Object Invocations', 'ARM Object Invocations', 'Accessing the ARM VSpace', 'Accessing CSpace', 'Accessing the Kernel Heap', 'Basic Kernel and Exception Monads', 'Abstract Specification Instantiations', 'Basic Data Structures', 'Machine Operations', 'ARM-Specific Data Types', 'ARM-Specific Virtual-Memory Rights', 'Access Rights', 'Error and Fault Messages', 'Machine Accessor Functions', 'ARM Machine Instantiation', 'Common, Architecture-Specific Data Types', 'Kernel Events', 'Machine Types', 'ARM Machine Types', 'Platform Definitions', 'Machine Word Setup', 'Enumeration instances for Words', 'Enumerations', 'Nondetermin

/tmp/ipykernel_2071684/757028785.py:24: DeprecationWarning: read_transaction has been renamed to execute_read
  related_nodes = session.read_transaction(get_specify_related_nodes)


In [5]:
# 初始化本地模型
from langchain_community.chat_models import ChatOllama
llm = ChatOllama(model='llama3.1:70b', temperature=0,num_ctx=12288)
json_llm = ChatOllama(model='llama3.1:70b', temperature=0,format='json',num_ctx=12288)

In [68]:
question = """[Origin Specification Tree] maintains a tree structure among specifications, with nodes at the same depth having similar granularity. 
    Please update the [Origin Specification Tree] according to the [contexts].
    if specification A in the [contexts] starts with (Code), adding "(Code)specification A" to the [Origin Specification Tree] in appropriate level.
    if specification A in the [contexts] starts with (Both), adding (Both) to the corresponding specification in the [Origin Specification Tree].
    Respond only with the final updated [Origin Specification Tree] in json format, with no additional commentary. Don't change the highest level of the [Origin Specification Tree].
    Make sure that your answer follows the following format, contains "name" and "children" 2 keys: 
{
  "name": "",
  "children": [
    {
      "name": "",
      "children": []
    },
    {
      "name": "",
      "children": []
    }
  ]
}
    [Origin Specification Tree]:
    {
  "name": "Nondeterministic State Monad with Failure",
  "children": [
    {
      "name": "Basic exception reasoning",
      "children": [
        {
          "name": "Determinism: Define a monad as deterministic if it returns exactly one result and does not fail. Ensure that the `det` predicate holds for `return x` and that the composition of deterministic monads using `bind` remains deterministic. This ensures that deterministic computations can be reasoned about in a straightforward manner.",
          "children": []
        },
        {
          "name": "Non-Failure and Validity: Define `no_fail P m` to check that a monad does not fail under a given precondition `P`. Also, define `validE` to specify validity for both normal and exceptional postconditions. Ensure that `no_fail` and `validE` are correctly applied to `returnOk` and `throwError` to verify their behavior under preconditions and postconditions.",
          "children": []
        },
        {
          "name": "Monad Laws for Exception Handling: Ensure that the left identity law (`returnOk x >>=E f = f x`), right identity law (`m >>=E returnOk = m`), and associativity law (`(m >>=E f) >>=E g = m >>=E (λx. f x >>=E g)`) hold for the exception monad. These laws ensure that the monadic operations behave as expected and can be composed reliably.",
          "children": []
        },
        {
          "name": "Exception Handling: Define `throwError` to set the failure flag and return an empty set of results, and `catch` to handle exceptions by providing a fallback computation if an exception is thrown. Ensure that `catch` checks the failure flag and applies the handler function if necessary.",
          "children": []
        }
      ]
    },
    {
      "name": "Hoare Logic",
      "children": [
        {
          "name": "Non-Failure",
          "children": [
            {
              "name": "Code Extension: The code can be extended arbitrarily, useful for showing that a larger set of code is also sufficient. This is formalized as: `{[P]} c {[Q]} ⟹ {[P]} (c ;; e) {[Q]}`.",
              "children": []
            },
            {
              "name": "Moving Pure Conditions: Pure stateless assertions can be pulled out of the precondition, useful for separating pure and impure parts of the logic. This is formalized as: `{[P * b]} c {[Q]} ⟹ (b ⟶ {[P]} c {[Q]})`.",
              "children": []
            },
            {
              "name": "Existential Quantifiers in Preconditions: Existential quantifiers in the precondition are equivalent to universal quantifiers outside of the specification, useful for dealing with existential conditions. This is formalized as: `{[∃x. P x]} c {[Q]} ⟹ {∀x. [P x]} c {[Q]}`.",
              "children": []
            },
            {
              "name": "Precondition Strengthening and Postcondition Weakening: Precondition strengthening and postcondition weakening rules, useful for refining and generalizing Hoare triples. These are formalized as: `{[P']} c {[Q]} ⟹ (P ⟶ P') ⟹ {[P]} c {[Q]}` and `{[P]} c {[Q']} ⟹ (Q' ⟶ Q) ⟹ {[P]} c {[Q]}`.",
              "children": []
            },
            {
              "name": "Composition Rule: The composition rule composes two specifications and takes the union of the two code sets, useful for reasoning about sequences of commands. This is formalized as: `{[P]} c1 {[Q]} ⟹ {[Q]} c2 {[R]} ⟹ {[P]} (c1 ;; c2) {[R]}`.",
              "children": []
            },
            {
              "name": "Frame Rule: The frame rule allows any assertions to be added to the pre- and postconditions of a Hoare triple, useful for modular reasoning. This is formalized as: `{[P]} c {[Q]} ⟹ {[P * R]} c {[Q * R]}`.",
              "children": []
            },
            {
              "name": "Lifting Logical Connectives: Lifting logical connectives over two arguments, useful for combining preconditions and postconditions. Examples include `bipred_conj P Q ≡ λx y. P x y ∧ Q x y` and `bipred_disj P Q ≡ λx y. P x y ∨ Q x y`.",
              "children": []
            },
            {
              "name": "Trivial Preconditions and Postconditions: Abbreviations for trivial preconditions and postconditions, useful for simplifying reasoning in proofs. Examples include `top ≡ λ_. True`, `bottom ≡ λ_. False`, `toptop ≡ λ_ _. True`, and `botbot ≡ λ_ _. False`.",
              "children": []
            },
            {
              "name": "Transformation to Ensure Empty Fail: A function to transform a result set and failure flag to ensure the empty_fail property. This is formalized as: `mk_ef S ≡ (fst S, fst S = {} ∨ snd S)`.",
              "children": []
            },
            {
              "name": "Empty Result Set Implies Failure: If a monad returns an empty set of results, it will have the failure flag set. This is formalized as: `empty_fail m ≡ ∀ s. fst (m s) = {} −→ snd (m s)`.",
              "children": []
            },
            {
              "name": "Validity and Non-Failure for Exception Monads: A monad `f` is valid and does not fail under a precondition `P`, with separate postconditions for normal and exceptional results. This is formalized as: `validE_NF P f Q E ≡ validE P f Q E ∧ no_fail P f`.",
              "children": []
            },
            {
              "name": "Validity and Non-Failure: A monad `f` is valid and does not fail under a precondition `P` and postcondition `Q`. This is formalized as: `validNF P f Q ≡ valid P f Q ∧ no_fail P f`.",
              "children": []
            },
            {
              "name": "Non-Failure: A monad `m` does not fail under a precondition `P` if, for no start state in that precondition, it sets the failure flag. This is formalized as: `no_fail P m ≡ ∀ s. P s *−→ ¬* (snd (m s))`.",
              "children": []
            }
          ]
        },
        {
          "name": "Determinism",
          "children": [
            {
              "name": "Deterministic Validity of Hoare Triples: For a given precondition P, monad f, and postcondition Q, the validity of the Hoare triple should be deterministic, meaning that the validity should not depend on non-deterministic factors. Formally, `∀P f Q. valid P f Q = valid P f Q`.",
              "children": []
            },
            {
              "name": "Deterministic When and Unless Operations: The when and unless operations should behave deterministically, meaning that for a given state s and a given condition P, the result should always be the same. Formally, `∀P m s. when P m s = when P m s` and `∀P m s. unless P m s = unless P m s`.",
              "children": []
            },
            {
              "name": "Deterministic Gets and Modify Operations: The gets and modify operations should behave deterministically, meaning that for a given state s and a given function f, the result should always be the same. Formally, `∀f s. gets f s = gets f s` and `∀f s. modify f s = modify f s`.",
              "children": []
            },
            {
              "name": "Deterministic Condition Handling: The condition function should behave deterministically, meaning that for a given state s, the same condition P and the same monads L and R, the result should always be the same. Formally, `∀P L R s. (condition P L R) s = (condition P L R) s`.",
              "children": []
            },
            {
              "name": "Deterministic State Transformation: The transformation of the state via the trans_state function should be deterministic, meaning that applying the same transformation function t to the same state s should always yield the same result. Formally, `∀t s. trans_state t s = trans_state t s`.",
              "children": []
            },
            {
              "name": "Deterministic Capability Deletion: During a revoke system call, the order in which capabilities are deleted should be consistent and predictable. Formally, `deterministic_capability_deletion s ≡ (∀cap_list1 cap_list2. (revoke s = cap_list1 ∧ revoke s = cap_list2) → cap_list1 = cap_list2)`.",
              "children": []
            },
            {
              "name": "Deterministic Scheduler: The scheduler should always select the same thread to run next, given the same state. Formally, `deterministic_scheduler s ≡ (∀t1 t2. (scheduler s = t1 ∧ scheduler s = t2) → t1 = t2)`.",
              "children": []
            },
            {
              "name": "Deterministic Execution: For a given command C and an initial state s, if the command is deterministic, then it should produce a single, unique final state s' and return value r. Formally, `deterministic_execution f ≡ ∀s. let (res, _) = f s in case res of [] => False | [(_, s')] => True | _ => False`.",
              "children": []
            }
          ]
        },
        {
          "name": "Validity",
          "children": []
        }
      ]
    },
    {
      "name": "Catching and Handling Exceptions",
      "children": [
        {
          "name": "Loops",
          "children": [
            {
              "name": "Exception Handling and Global Variables: The loop should correctly handle exceptions and update the global exception variable `global-exn-var` as needed. It should catch and handle exceptions using the TRY-CATCH mechanism, updating `global-exn-var` with the appropriate exception code. The `global-exn-var` should be set to `EXCEPTION_NONE` if the loop completes normally, or to the appropriate exception code if an exception occurs.",
              "children": []
            },
            {
              "name": "Precision and Loss of Conditional Information: The loop should minimize the loss of conditional information, especially during procedure calls. The number of conditions dropped during procedure calls should be tracked and minimized to ensure the loop remains as precise as possible, and any loss of precision should be documented and justified.",
              "children": []
            },
            {
              "name": "Loop Invariant Preservation: The loop invariant should be preserved throughout the execution of the loop. The invariant should be true before the loop starts, remain true after each iteration, and be true when the loop terminates.",
              "children": []
            },
            {
              "name": "Non-Interference with External State: The loop should not interfere with external state unless explicitly allowed by the guards and conditions. It should only write to memory addresses that are safe and aligned, as determined by the memory safety guards. The heap should be updated only if the write-safety conditions are met, ensuring that the loop does not corrupt the heap.",
              "children": []
            },
            {
              "name": "State Precondition and Return Value Relations: The loop should maintain the state preconditions and return value relations as specified by the correspondence statement. The initial states `s` and `t` must satisfy the preconditions `P` and `P'`. The return value from the loop should be related to the abstract specification's return value via the return value relation `r`, and extracted using the extraction function `xf`.",
              "children": []
            },
            {
              "name": "Handler Stack Execution: If the loop terminates abruptly due to a `return`, `continue`, or `break` statement, the handler stack should be executed in sequence until one of the handlers terminates normally. For `return`, the loop should handle the return value and execute the handler stack for cleanup. For `continue` and `break`, the handler stack should manage abrupt termination.",
              "children": []
            },
            {
              "name": "Loop Termination and Exception Handling: The loop should terminate correctly when a `break` or `continue` statement is encountered. If a `break` is executed, the loop should terminate immediately, and control should be transferred to the next statement after the loop. If a `continue` is executed, the current iteration should be terminated, and the loop should proceed to the next iteration.",
              "children": []
            }
          ]
        }
      ]
    },
    {
      "name": "Library of Monadic Functions and Combinators",
      "children": [
        {
          "name": "Exception Handling Combinators: Define `sequenceE_x`, `mapME_x`, `sequenceE`, and `mapME` for exception handling. Ensure they handle empty lists and cons cases, and ensure non-failure. For example, `sequenceE_x [] = returnOk ()`, `sequenceE_x (m # ms) = m >>=E (λ_. sequenceE_x ms)`, and `no_fail P (sequenceE_x ms) ⟷ (∀m ∈ set ms. no_fail P m)`. Similarly, define and ensure properties for `mapME_x`, `sequenceE`, and `mapME`.",
          "children": []
        },
        {
          "name": "Folding a Monadic Function: Define `foldM` to fold a monadic function over a list. Ensure it handles empty lists and cons cases: `foldM m [] a = return a` and `foldM m (x # xs) a = foldM m xs a >>= m x`. Also, ensure non-failure: `no_fail P (foldM m xs a) ⟷ (∀x ∈ set xs. no_fail P (m x a))`.",
          "children": []
        },
        {
          "name": "Filtering a List with a Monadic Predicate: Define `filterM` to filter a list using a monadic predicate. Ensure it handles empty lists and cons cases: `filterM P [] = return []` and `filterM P (x # xs) = P x >>= (λb. filterM P xs >>= (λys. return (if b then (x # ys) else ys)))`. Also, ensure non-failure: `no_fail P (filterM Q xs) ⟷ (∀x ∈ set xs. no_fail P (Q x))`.",
          "children": []
        },
        {
          "name": "Mapping a Monadic Function with Results: Define `mapM` to map a monadic function over a list, returning a list of results. Ensure it handles empty lists and cons cases: `mapM f [] = return []` and `mapM f (x # xs) = f x >>= (λy. mapM f xs >>= (λys. return (y # ys)))`. Also, ensure non-failure: `no_fail P (mapM f xs) ⟷ (∀x ∈ set xs. no_fail P (f x))`.",
          "children": []
        },
        {
          "name": "Sequence of Monads with Results: Define `sequence` to run a sequence of monads, returning a list of results. Ensure it handles empty lists and cons cases: `sequence [] = return []` and `sequence (m # ms) = m >>= (λx. sequence ms >>= (λxs. return (x # xs)))`. Also, ensure non-failure: `no_fail P (sequence ms) ⟷ (∀m ∈ set ms. no_fail P m)`.",
          "children": []
        },
        {
          "name": "Zipping Two Lists with a Monadic Function: Define `zipWithM_x` to zip two lists with a monadic function, ignoring return values. Ensure it handles empty lists and cons cases: `zipWithM_x f [] [] = return ()` and `zipWithM_x f (x # xs) (y # ys) = f x y >>= (λ_. zipWithM_x f xs ys)`. Also, ensure non-failure: `no_fail P (zipWithM_x f xs ys) ⟷ (∀(x, y) ∈ set (zip xs ys). no_fail P (f x y))`.",
          "children": []
        },
        {
          "name": "Mapping a Monadic Function: Define `mapM_x` to map a monadic function over a list, ignoring return values. Ensure it handles empty lists and cons cases: `mapM_x f [] = return ()` and `mapM_x f (x # xs) = f x >>= (λ_. mapM_x f xs)`. Also, ensure non-failure: `no_fail P (mapM_x f xs) ⟷ (∑x ∈ set xs. no_fail P (f x))`.",
          "children": []
        },
        {
          "name": "Running a Sequence of Monads: Define `sequence_x` to run a sequence of monads from left to right, ignoring return values. Ensure it handles empty lists and cons cases: `sequence_x [] = return ()` and `sequence_x (m # ms) = m >>= (λ_. sequence_x ms)`. Also, ensure non-failure: `no_fail P (sequence_x ms) ⟷ (∀m ∈ set ms. no_fail P m)`.",
          "children": []
        },
        {
          "name": "Lifting a Normal Function: Define `liftM` to lift a normal function into the monad type. Ensure it satisfies the identity and composition laws: `liftM id m = m` and `liftM (g ∘ f) m = liftM g (liftM f m)`.",
          "children": []
        }
      ]
    },
    {
      "name": "Syntax",
      "children": [
        {
          "name": "Syntax for the Exception Monad",
          "children": [
            {
              "name": "Hoare Logic: The `validE` predicate should correctly capture the behavior of the exception monad, ensuring that both normal and exceptional postconditions are satisfied. The `validE_R` and `validE_E` predicates should correctly separate reasoning for normal and exceptional cases, ensuring that the appropriate postcondition is applied based on the type of result.",
              "children": []
            },
            {
              "name": "Sequence and Map Operations: The `sequenceE` operation should sequence a list of monads, collecting their results in a list. The `mapME` operation should map a monadic function over a list, collecting the results in a list, ensuring that the sequence and map operations maintain the structure and order of the results.",
              "children": []
            },
            {
              "name": "Lifting Functions: The `liftE` operation should lift a normal nondeterministic monad into the exception monad, always returning the result as a normal result. The `liftME` operation should lift a function over the exception monad, applying the function to the result if it is a normal value.",
              "children": []
            },
            {
              "name": "Catching and Handling Exceptions: The `catch` operation should catch and handle exceptions, returning the result of the handler if an exception is thrown. The `handle_elseE` operation should handle exceptions and provide a continuation if no exception is thrown, ensuring that the handler is executed with the exception and the continuation with the normal result.",
              "children": []
            },
            {
              "name": "Conditional Execution: The `whenE` and `unlessE` operations should execute the monad only if the condition is true or false, respectively. Specifically, `whenE P m` should be equivalent to `m` if `P` is true, and `returnOk ()` otherwise. Similarly, `unlessE P m` should be equivalent to `returnOk ()` if `P` is true, and `m` otherwise.",
              "children": []
            },
            {
              "name": "Return and Throw Operations: The `returnOk` operation should wrap a value in the right part of the sum type, while the `throwError` operation should wrap an exception in the left part of the sum type.",
              "children": []
            },
            {
              "name": "Exception Handling and Propagation: The `bindE` operation should propagate exceptions, ensuring that the right-hand side is not executed if the left-hand side throws an exception. The `handleE` operation should correctly handle exceptions by executing the handler with the exception as input.",
              "children": []
            }
          ]
        },
        {
          "name": "Syntax for the Nondeterministic State Monad",
          "children": [
            {
              "name": "Lifting Logical Connectives: Lifting logical connectives over two arguments. Conjunction: bipred_conj P Q ≡ λx y. P x y ∧ Q x y. Disjunction: bipred_disj P Q ≡ λx y. P x y ∨ Q x y",
              "children": []
            },
            {
              "name": "Trivial Preconditions and Postconditions: Abbreviations for trivial preconditions and postconditions. Top: > ≡ λ_. True. Bottom: ⊥ ≡ λ_. False. Toptop: >> ≡ λ_ _. True. Botbot: ⊥⊥ ≡ λ_ _. False",
              "children": []
            },
            {
              "name": "Exception Handling: The `validE` definition should handle both normal and exceptional results. Formalization: {|P|} f {|Q|},{|E*|} ≡ ∀s. P s → (∀v s'. (case v of Inr r ⇒ Q r s' | Inl e ⇒ E e s') ∧ (v, s') ∈ fst (f s))",
              "children": []
            },
            {
              "name": "Hoare Logic: A Hoare triple {|P|} f {|Q*|} should be valid if for all states satisfying the precondition P, all result values and result states returned by the monad satisfy the postcondition Q. Formalization: {|P|} f {|Q*|} ≡ ∀s. P s → (∀ (r, s') ∈ fst (f s). Q r s')",
              "children": []
            },
            {
              "name": "Failure Flag: The failure flag should be set if any part of the computation fails. Formalization: ∀s. snd ((f >>= g) s) = (snd (f s) ∨ (∃ (r, s') ∈ fst (f s). snd (g r s')))",
              "children": []
            },
            {
              "name": "Monad Laws: The monad should satisfy the left identity, right identity, and associativity laws. Left Identity: (return x >>= f) = f x. Right Identity: (m >>= return) = m. Associativity: (m >>= f) >>= g = m >>= (λx. f x >>= g)",
              "children": []
            },
            {
              "name": "Bind Operation: The `bind` operation should correctly chain two monadic operations, ensuring that the result of the first operation is passed to the second. Formalization: (f >>= g) ≡ λs. ({(r'', s''). ∃ (r', s') ∈ fst (f s). (r'', s'') ∈ fst (g r' s')}, snd (f s) ∨ (∃ (r', s') ∈ fst (f s). snd (g r' s')))",
              "children": []
            },
            {
              "name": "Return Operation: The `return` operation should not change the state and should not fail. Formalization: ∀s. (return x) s = ({(x, s)}, False)",
              "children": []
            }
          ]
        }
      ]
    },
    {
      "name": "Adding Exceptions",
      "children": [
        {
          "name": "Monad Laws for the Exception Monad",
          "children": [
            {
              "name": "Catching and Handling Exceptions: The `<catch>` and `<handle>` functions should correctly catch and handle exceptions. The `<catch>` function should turn an exception monad into a normal state monad by catching and handling any potential exceptions, while the `<handle>` function should stay within the exception monad and handle exceptions, potentially throwing a different type of exception. Formalizations: `f <catch> handler = do x ← f; case x of Inr b ⇒ return b | Inl e ⇒ handler e od` and `f <handle> handler = do v ← f; case v of Inl e ⇒ handler e | Inr v' ⇒ return (Inr v') od`.",
              "children": []
            },
            {
              "name": "Conditional Execution: The `whenE` and `unlessE` functions should conditionally execute the given monad based on a boolean condition. `whenE` should execute the monad if the condition is true, otherwise return `returnOk ()`. `unlessE` should execute the monad if the condition is false and return `returnOk ()` if the condition is true. Formalizations: `whenE P f = (if P then f else returnOk ())` and `unlessE P f = (if P then returnOk () else f)`.",
              "children": []
            },
            {
              "name": "Lifting Normal Monads: The `liftE` function should lift a normal nondeterministic monad into the exception monad, ensuring that the result is always returned as a normal result and never throws an exception. Formalization: `liftE m = m >>= (λr. return (Inr r))`.",
              "children": []
            },
            {
              "name": "Exception Handling: The `throwError` function should throw an exception, and the `handleE` function should catch and handle that exception. If the exception is caught, the handler should be executed. Formalization: `throwError e <handle> h = h e`.",
              "children": []
            },
            {
              "name": "Associativity Law: The `bindE` operation should be associative, meaning that the order in which binds are evaluated should not matter. Formalization: `(m >>=E f) >>=E g = m >>=E (λx. f x >>=E g)`.",
              "children": []
            },
            {
              "name": "Right Identity Law: The `returnOk` function should be a right identity for `bindE`, meaning that binding a monadic value with `returnOk` should return the original monadic value. Formalization: `m >>=E returnOk = m`.",
              "children": []
            },
            {
              "name": "Left Identity Law: The `returnOk` function should be a left identity for `bindE`, meaning that wrapping a value in `returnOk` and then binding it with a function should yield the same result as applying the function directly to the value. Formalization: `returnOk x >>=E f = f x`.",
              "children": []
            }
          ]
        }
      ]
    },
    {
      "name": "The Monad",
      "children": [
        {
          "name": "The Monad Laws",
          "children": [
            {
              "name": "Bipredicate Conjunction and Disjunction: Bipredicate conjunction and disjunction should be defined as: `bipred_conj P Q ≡ λ x y. P(x, y) ∧ Q(x, y)` and `bipred_disj P Q ≡ λ x y. P(x, y) ∨ Q(x, y)`.",
              "children": []
            },
            {
              "name": "Trivial Preconditions and Postconditions: Define trivial preconditions and postconditions as: `top ≡ λ _. True`, `bottom ≡ λ _. False`, `toptop ≡ λ _ _. True`, and `botbot ≡ λ _ _. False`.",
              "children": []
            },
            {
              "name": "Separate Validity for Normal and Exceptional Cases: Separate validity for normal and exceptional cases should be defined as: `{P} f {Q}, - ≡ {P} f {Q, λ x y. True}` and `{P} f -, {E} ≡ {P} f {λ x y. True, E}`.",
              "children": []
            },
            {
              "name": "Validity for Exception Monad: The validity of a Hoare triple for the exception monad should be defined as: `{P} f {Q, E} ≡ {P} f {λ v s. case v of Inr r => Q(r, s) | Inl e => E(e, s)}`.",
              "children": []
            },
            {
              "name": "Validity for Nondeterministic State Monad: The validity of a Hoare triple for the nondeterministic state monad should be defined as: `{P} f {Q} ≡ ∀ s. P(s) → (∀ (r, s') ∈ fst(f(s)). Q(r, s'))`.",
              "children": []
            },
            {
              "name": "Exception Handling: The `catch` operation should handle exceptions by providing a fallback function: `catch m h ≡ m >>= (\\v. case v of Inl e => h(e) | Inr r => returnOk r)`.",
              "children": []
            },
            {
              "name": "Error Monad: Define the error monad with `('s, 'a, 'b) error_monad = ('s, 'a + 'b) state_monad`, `returnOk a ≡ return (Inr a)`, `throwError e ≡ return (Inl e)`, `lift f v ≡ case v of Inl e => throwError e | Inr v' => f v'`, and `f >>=E g ≡ f >>= lift g`.",
              "children": []
            },
            {
              "name": "Modify Operation: The `modify` operation should update the state using a given function: `modify f ≡ \\s. ((), f(s))`.",
              "children": []
            },
            {
              "name": "Get Operation: The `gets` operation should retrieve the current state without modifying it: `gets f ≡ \\s. (f(s), s)`.",
              "children": []
            },
            {
              "name": "State Transformer Monad: Define the state transformer monad with `('s, 'a) state_monad = 's => ('a × 's)`, `return a ≡ \\s. (a, s)`, and `f >>= g ≡ \\s. let (v, s') = f s in g v s'`.",
              "children": []
            },
            {
              "name": "Associativity Law: For any monadic value `m` and functions `f` and `g`, the following should hold: `(m >>= f) >>= g = m >>= (\\x. f x >>= g)`.",
              "children": []
            },
            {
              "name": "Right Identity Law: For any monadic value `m`, the following should hold: `m >>= return = m`.",
              "children": []
            },
            {
              "name": "Left Identity Law: For any value `x` and function `f`, the following should hold: `(return x >>= f) = f(x)`.",
              "children": []
            }
          ]
        },
        {
          "name": "Generic functions on top of the state monad",
          "children": [
            {
              "name": "Bipredicate Conjunction and Disjunction: Combine bipredicates using conjunction and disjunction. bipred_conj P Q ≡ λx y. P x y ∧ Q x y and bipred_disj P Q ≡ λx y. P x y ∨ Q x y.",
              "children": []
            },
            {
              "name": "Trivial Preconditions and Postconditions: Define top, bottom, toptop, and botbot as trivial predicates. top ≡ λ_. True, bottom ≡ λ_. False, toptop ≡ λ_ _. True, and botbot ≡ λ_ _. False.",
              "children": []
            },
            {
              "name": "Hoare Logic for Partial Correctness: Define validity for nondeterministic state monad and exception monad. For the state monad, valid P f Q ≡ ∀s. P s → (∀(r, s') ∈ fst (f s). Q r s'). For the exception monad, validE P f Q E ≡ valid P f (λv s. case v of Inr r ⇒ Q r s | Inl e ⇒ E e s).",
              "children": []
            },
            {
              "name": "Filtering with Monadic Predicate: Implement filterM to filter a list using a monadic predicate. filterM P [] = return [] and filterM P (x # xs) = do b <- P x; ys <- filterM P xs; return (if b then (x # ys) else ys) od.",
              "children": []
            },
            {
              "name": "Fold Operation: Define foldM to fold a monadic function over a list with an initial accumulator, using foldr (λp q. q >>= m p) xs (return a).",
              "children": []
            },
            {
              "name": "Sequence and Map with Ignored Return Values: Use sequence_x, mapM_x, and zipWithM_x to run a sequence of monads, apply a monadic function to each element of a list, and apply a monadic function to pairs of elements from two lists, respectively, while ignoring the return values.",
              "children": []
            },
            {
              "name": "Sequence and Map Operations: Implement sequence, mapM, and zipWithM to run a sequence of monads, apply a monadic function to each element of a list, and apply a monadic function to pairs of elements from two lists, respectively. Collect the results into a list.",
              "children": []
            },
            {
              "name": "Lifting Functions: Define liftM and liftME to lift normal and exception-handling functions into the monad, respectively. liftM f m ≡ do x ← m; return (f x) od and liftME f m ≡ doE x ← m; returnOk (f x) odE.",
              "children": []
            },
            {
              "name": "Monad Laws: Ensure the monad laws are satisfied, including Left Identity (return x >>= f = f x), Right Identity (m >>= return = m), and Associativity ((m >>= f) >>= g = m >>= (λx. f x >>= g)).",
              "children": []
            }
          ]
        },
        {
          "name": "Failure",
          "children": [
            {
              "name": "Hoare Logic Validity: A triple is valid if for all states that satisfy the precondition, all result values and result states that are returned by the monad satisfy the postcondition. Definition: `{|P|} f {|Q*|} ≡ ∀* s. P s −→ (∀ (r,s') ∈ fst (f s). Q r s')`. Validity for the exception monad with two postconditions: one for normal and one for exceptional results. Definition: `{|P|} f {|Q|},{|E*|} ≡ {|*P|} f {| λv s. case v of Inr r ⇒ Q r s | Inl e ⇒ E e s |}`.",
              "children": []
            },
            {
              "name": "Exception Handling: The `cap_fault_on_failure` function lifts a lookup failure monad into a fault monad by converting the error into a `CapFault`. Definition: `cap_fault_on_failure cptr rp m ≡ handleE' m (throwError ◦ CapFault cptr rp)`. The `lookup_error_on_failure` function lifts a lookup failure monad into a system call error monad by converting the error into a `FailedLookup`. Definition: `lookup_error_on_failure s m ≡ handleE' m (throwError ◦ FailedLookup s)`.",
              "children": []
            },
            {
              "name": "Monad Laws with Failure: The `return` function is absorbed at the left of a `bind` operation, applying the return value directly. Law: `(return x >>= f) = f x`. The `return` function is absorbed on the right of a `bind` operation. Law: `(m >>= return) = m`. The `bind` operation is associative. Law: `(m >>= f) >>= g = m >>= (λx. f x >>= g)`.",
              "children": []
            },
            {
              "name": "Empty Fail: If a monad returns an empty set of results, it must have the failure flag set. Definition: `empty_fail m ≡ ∀ s. fst (m s) = {} −→ snd (m s)`.",
              "children": []
            },
            {
              "name": "ValidNF: A monad `f` is valid and non-failing under a precondition `P` and postcondition `Q`. Definition: `validNF P f Q ≡ valid P f Q ∧ no_fail P f`.",
              "children": []
            },
            {
              "name": "Non-Failure: A monad `m` does not fail under a precondition `P` if for no start state in that precondition it sets the failure flag. Definition: `no_fail P m ≡ ∀ s. P s *−→ ¬* (snd (m s))`.",
              "children": []
            },
            {
              "name": "State Assertion: The `state_assert` function introspects the current state and fails if the given state predicate `P` is not true. Definition: `state_assert P ≡ get >>= (λs. assert (P s))`.",
              "children": []
            },
            {
              "name": "Assertion: The `assert` function fails if the given property `P` is not true; otherwise, it returns `()`. Definition: `assert P ≡ if P then return () else fail`. The `assert_opt` function fails if the value is `None`, and returns the result `v` for `Some v`. Definition: `assert_opt v ≡ case v of None ⇒ fail | Some v ⇒ return v`.",
              "children": []
            },
            {
              "name": "Failure Monad: The `fail` function always fails, returning an empty set of results and setting the failure flag. Definition: `fail ≡ λs. ({}, True)`.",
              "children": []
            }
          ]
        },
        {
          "name": "Nondeterminism",
          "children": [
            {
              "name": "Bipredicate Conjunction and Disjunction: Allows combining two predicates over two arguments using logical conjunction and disjunction. Conjunction is defined as `bipred_conj P Q ≡ λx y. P x y ∧ Q x y`. Disjunction is defined as `bipred_disj P Q ≡ λx y. P x y ∨ Q x y`.",
              "children": []
            },
            {
              "name": "Trivial Preconditions and Postconditions: Abbreviations for trivial preconditions and postconditions. `top` represents a trivial true condition, defined as `> ≡ λ_. True`. `bottom` represents a trivial false condition, defined as `⊥ ≡ λ_. False`.",
              "children": []
            },
            {
              "name": "Exception Handling Validity: Extends the validity to handle exceptions. Provides separate postconditions for normal and exceptional results. Defined as `{|P|} f {|Q|},{|E*|} ≡ {|*P|} f {| λv s. case v of Inr r ⇒ Q r s | Inl e ⇒ E e s |}`.",
              "children": []
            },
            {
              "name": "Hoare Logic Validity: Defines the validity of a Hoare triple. Ensures that for all states satisfying the precondition `P`, the results and states returned by the computation `f` satisfy the postcondition `Q`. Defined as `{|P|} f {|Q*|} ≡ ∀* s. P s −→ (∀ (r,s') ∈ fst (f s). Q r s')`.",
              "children": []
            },
            {
              "name": "Bind Operation: Sequences two monadic computations. Applies the function `g` to the result of `f` and combines their results. The failure flag is set if either `f` or `g` fails. Defined as `bind f g ≡ λs. (S(fst ' split g ' fst (f s)), True ∈ snd ' split g ' fst (f s) ∨ snd (f s))`.",
              "children": []
            },
            {
              "name": "State Access and Modification: Basic operations for accessing and modifying the state. `get` retrieves the current state, defined as `get ≡ λs. ({(s,s)}, False)`. `put` sets the state to a new value, defined as `put s ≡ λ_. ({((),s)}, False)`.",
              "children": []
            },
            {
              "name": "Monad Laws: Fundamental laws for monad operations. Includes Left Identity (`return a >>= f = f a`), Right Identity (`m >>= return = m`), and Associativity (`(m >>= f) >>= g = m >>= (λx. f x >>= g)`).",
              "children": []
            },
            {
              "name": "Empty Failure Property: Ensures that if a computation returns an empty set of results, the failure flag is set. Defined as `empty_fail m ≡ ∀ s. fst (m s) = {} −→ snd (m s)`.",
              "children": []
            },
            {
              "name": "Validity with Non-Failure: Combines the validity of a Hoare triple with the non-failure property. Ensures that the computation `f` satisfies the postcondition `Q` and does not fail under the precondition `P`. Defined as `validNF P f Q ≡ valid P f Q ∧ no_fail P f`.",
              "children": []
            },
            {
              "name": "Non-Failure Property: Ensures that a computation `m` does not fail under a given precondition `P`. Defined as `no_fail P m ≡ ∀ s. P s −→ ¬ (snd (m s))`.",
              "children": []
            }
          ]
        }
      ]
    }
  ]
}
    [contexts]:
    context:{
    "name": "(Both)Nondeterministic State Monad with Failure"
}
context:```json
{
    "name": "(Code)Type Abbreviation for Nondeterministic State Monad with Failure: Provides a more readable and concise type syntax for the nondeterministic state monad with failure, ensuring that the state variable occurs twice in the type."
}
```
context:{
    "name": "(Code)Return Function: The return function in the nondeterministic state monad with failure does not alter the state, does not fail, and returns the specified value."
}
context:{
    "name": "(Code)Nondeterministic Binding with Failure: The bind operation combines two monadic actions, where the second action is dependent on the result of the first. The combined operation's result is the union of all possible outcomes from applying the second action to each outcome of the first. The combined operation may fail if either the first action fails or the second action fails for any of the results of the first."
}
context:```json
{
    "name":"(Code)Reversed Bind Operation: Allows the composition of monadic actions in a reversed order, providing flexibility in writing and understanding monadic bindings."
}
```
context:{
    "name": "(Both)State Access and Modification: Basic operations for accessing and modifying the state. `get` retrieves the current state, defined as `get ≡ λs. ({(s,s)}, False)`. `put` sets the state to a new value, defined as `put s ≡ λ_. ({((),s)}, False)`."
}
context:```json
{
    "name": "(Code)Nondeterministic Choice with Failure: The system allows for the selection of an element from a set and the nondeterministic choice between two operations. The selection does not change the state and does not fail, even if the set is empty. The alternative operation returns the union of the results of the two operations and may fail if either operation can fail."
}
```
context:```json
{
    "name":"(Code)Nondeterministic Selection with Failure: Allows the selection of a value from a set, paired with a boolean indicating whether the execution has failed. This enables the lifting of monads between different state spaces while preserving failure information."
}
```
context:```json
{
    "name":"(Code)Nondeterministic State Selection: Selects a state nondeterministically from a set of states related to the input state according to a given relationship. Fails if no such related state exists."
}
```
context:{
    "name": "(Both)Exception Handling: Define `throwError` to set the failure flag and return an empty set of results, and `catch` to handle exceptions by providing a fallback computation if an exception is thrown. Ensure that `catch` checks the failure flag and applies the handler function if necessary."
}
context:{
  "name": "(Code)Property: Assertion Validation: Ensures that a given property \( P \) holds, failing the computation if \( P \) is not true."
}
context:```json
{
  "name": "(Code)property:Assertion with Optional Values: Ensures that the computation fails if the value is `None`, and returns the result `v` if the value is `Some v`."
}
```
context:{
    "name": "(Code)State Assertion with Introspection: Allows for the introspection of the current state and asserts a condition based on that state."
}
context:{
    "name":"(Code)State Retrieval: Retrieve the current state and apply a function to it, returning the result without modifying the state."
}
context:{
  "name": "(Code)State Modification: Allows the current state to be updated using a provided function, ensuring that the state transformation is encapsulated and applied atomically."
}
context:{
    "name": "(Both)Conditional Execution: The `whenE` and `unlessE` operations should execute the monad only if the condition is true or false, respectively. Specifically, `whenE P m` should be equivalent to `m` if `P` is true, and `returnOk ()` otherwise. Similarly, `unlessE P m` should be equivalent to `returnOk ()` if `P` is true, and `m` otherwise."
}
context:```json
{
    "name": "(Both)Conditional Execution: The `whenE` and `unlessE` functions should conditionally execute the given monad based on a boolean condition. `whenE` should execute the monad if the condition is true, otherwise return `returnOk ()`. `unlessE` should execute the monad if the condition is false and return `returnOk ()` if the condition is true. Formalizations: `whenE P f = (if P then f else returnOk ())` and `unlessE P f = (if P then returnOk () else f)`."
}
```
context:```json
{
  "name": "(Both)Conditional Execution: The `whenE` and `unlessE` operations should execute the monad only if the condition is true or false, respectively. Specifically, `whenE P m` should be equivalent to `m` if `P` is true, and `returnOk ()` otherwise. Similarly, `unlessE P m` should be equivalent to `returnOk ()` if `P` is true, and `m` otherwise."
}
```
context:```json
{
  "name": "(Code)Apply Option-Valued Function: Execute an option-valued function on the current state, failing if the result is `None` and returning the value `v` if the result is `Some v`."
}
```
context:{
  "name": "(Code)Retrieve Map Value: Access a map from the current state and apply a given argument to retrieve a value. If the map returns `None`, the operation fails; otherwise, it returns the retrieved value."
}
context:{
    "name":"(Both)Nondeterministic State Monad with Failure"
}
context:```json
{
  "name": "(Code)Return Absorption: The `return` function, when bound to another function `f`, directly applies the return value to `f`, effectively absorbing the `return` operation."
}
```
context:{
    "name":"(Both)Right Identity Law: The `returnOk` function should be a right identity for `bindE`, meaning that binding a monadic value with `returnOk` should return the original monadic value. Formalization: `m >>=E returnOk = m`."
}
context:{
    "name": "(Both)Associativity Law: The `bindE` operation should be associative, meaning that the order in which binds are evaluated should not matter. Formalization: `(m >>=E f) >>=E g = m >>=E (λx. f x >>=E g)`."
}
context:```json
{
    "name": "(Both)Exception Handling: Define `throwError` to set the failure flag and return an empty set of results, and `catch` to handle exceptions by providing a fallback computation if an exception is thrown. Ensure that `catch` checks the failure flag and applies the handler function if necessary."
}
```
context:{
    "name":"(Code)Lifting with Exception Handling: Lifts a function to handle exceptions, where if the input is an exception, it returns that exception; otherwise, it continues with the function execution."
}
context:```json
{
  "name": "(Both)Exception Handling: The `bindE` operation should propagate exceptions, ensuring that the right-hand side is not executed if the left-hand side throws an exception. The `handleE` operation should correctly handle exceptions by executing the handler with the exception as input."
}
```
context:{
    "name":"(Code)Lifting Nondeterministic Monad: Transforms a nondeterministic monad into an exception monad by wrapping its result in a normal result constructor, ensuring that no exceptions are thrown."
}
context:{
    "name": "(Both)Conditional Execution: The `whenE` and `unlessE` operations should execute the monad only if the condition is true or false, respectively. Specifically, `whenE P m` should be equivalent to `m` if `P` is true, and `returnOk ()` otherwise. Similarly, `unlessE P m` should be equivalent to `returnOk ()` if `P` is true, and `m` otherwise."
}
context:```json
{
  "name": "(Code)Exception Handling with Optional Values: Throws an exception if the input is `None`, otherwise returns the value wrapped in `Some`."
}
```
context:```json
{
    "name":"(Code)Assertion with Exceptional Failure: The `assertE` function checks a boolean condition and returns `returnOk ()` if the condition is true, otherwise it fails with an exception."
}
```
context:{
  "name": "(Both)Lift a Normal Function: Define `liftM` to lift a normal function into the monad type. Ensure it satisfies the identity and composition laws: `liftM id m = m` and `liftM (g ∘ f) m = liftM g (liftM f m)`."
}
context:{
    "name": "(Both)Monad Laws for Exception Handling: Ensure that the left identity law (`returnOk x >>=E f = f x`), right identity law (`m >>=E returnOk = m`), and associativity law (`(m >>=E f) >>=E g = m >>=E (λx. f x >>=E g)`) hold for the exception monad. These laws ensure that the monadic operations behave as expected and can be composed reliably."
}
context:{
  "name": "(Both)Right Identity Law: The `returnOk` function should be a right identity for `bindE`, meaning that binding a monadic value with `returnOk` should return the original monadic value. Formalization: `m >>=E returnOk = m`."
}
context:{
    "name": "(Both)Associativity Law: The `bindE` operation should be associative, meaning that the order in which binds are evaluated should not matter. Formalization: `(m >>=E f) >>=E g = m >>=E (λx. f x >>=E g)`."
}
context:```json
{
  "name": "(Both)Right Identity Law: The `returnOk` function should be a right identity for `bindE`, meaning that binding a monadic value with `returnOk` should return the original monadic value. Formalization: `m >>=E returnOk = m`."
}
```
context:```json
{
  "name": "(Code)Exception Propagation: Throwing an exception causes the subsequent execution to be skipped, ensuring that no further operations are performed after an exception is thrown."
}
```
context:{
    "name": "(Both)Nondeterministic State Monad with Failure"
}
context:```json
{
    "name": "(Both)Syntax for the Exception Monad"
}
```
context:```json
{
    "name":"(Both)Nondeterministic State Monad with Failure"
}
```
context:```json
{
    "name":"(Code)Exception Handling in Nondeterministic State Monad: Provides a syntax for handling exceptions within a monadic context, using the @{text doE}/@{text odE} notation to sequence operations and handle failures."
}
```
context:{
    "name": "(Both)Nondeterministic State Monad with Failure"
}
context:{
    "name": "(Both)Lift a Normal Function: Define `liftM` to lift a normal function into the monad type. Ensure it satisfies the identity and composition laws: `liftM id m = m` and `liftM (g ∘ f) m = liftM g (liftM f m)`."
}
context:{
    "name": "(Code)Lift Function in Exception Monad: Applies a function to the result of a monadic computation, wrapping the result in an `Ok` value within the exception monad."
}
context:{
    "name": "(Both)Conditional Execution: The `whenE` and `unlessE` operations should execute the monad only if the condition is true or false, respectively. Specifically, `whenE P m` should be equivalent to `m` if `P` is true, and `returnOk ()` otherwise. Similarly, `unlessE P m` should be equivalent to `returnOk ()` if `P` is true, and `m` otherwise."
}
context:{
  "name": "(Both)Running a Sequence of Monads: Define `sequence_x` to run a sequence of monads from left to right, ignoring return values. Ensure it handles empty lists and cons cases: `sequence_x [] = return ()` and `sequence_x (m # ms) = m >>= (λ_. sequence_x ms)`. Also, ensure non-failure: `no_fail P (sequence_x ms) ⟷ (∀m ∈ set ms. no_fail P m)`."
}
context:```json
{
  "name": "(Both)Map a Monadic Function with Results: Define `mapM` to map a monadic function over a list, returning a list of results. Ensure it handles empty lists and cons cases: `mapM f [] = return []` and `mapM f (x # xs) = f x >>= (λy. mapM f xs >>= (λys. return (y # ys)))`. Also, ensure non-failure: `no_fail P (mapM f xs) ⟷ (∀x ∈ set xs. no_fail P (f x))`."
}
```
context:{
    "name": "(Both)Zipping Two Lists with a Monadic Function: Define `zipWithM_x` to zip two lists with a monadic function, ignoring return values. Ensure it handles empty lists and cons cases: `zipWithM_x f [] [] = return ()` and `zipWithM_x f (x # xs) (y # ys) = f x y >>= (λ_. zipWithM_x f xs ys)`. Also, ensure non-failure: `no_fail P (zipWithM_x f xs ys) ⟷ (∀(x, y) ∈ set (zip xs ys). no_fail P (f x y))`."
}
context:{
    "name": "(Both)Exception Handling Combinators: Define `sequenceE_x`, `mapME_x`, `sequenceE`, and `mapME` for exception handling. Ensure they handle empty lists and cons cases, and ensure non-failure. For example, `sequenceE_x [] = returnOk ()`, `sequenceE_x (m # ms) = m >>=E (λ_. sequenceE_x ms)`, and `no_fail P (sequenceE_x ms) ⟷ (∀m ∈ set ms. no_fail P m)`. Similarly, define and ensure properties for `mapME_x`, `sequenceE`, and `mapME`."
}
context:```json
{
    "name": "(Both)Exception Handling Combinators: Define `sequenceE_x`, `mapME_x`, `sequenceE`, and `mapME` for exception handling. Ensure they handle empty lists and cons cases, and ensure non-failure. For example, `sequenceE_x [] = returnOk ()`, `sequenceE_x (m # ms) = m >>=E (λ_. sequenceE_x ms)`, and `no_fail P (sequenceE_x ms) ⟷ (∀m ∈ set ms. no_fail P m)`. Similarly, define and ensure properties for `mapME_x`, `sequenceE`, and `mapME`."
}
```
context:{
    "name":"(Both)Filtering with Monadic Predicate: Implement filterM to filter a list using a monadic predicate. filterM P [] = return [] and filterM P (x # xs) = do b <- P x; ys <- filterM P xs; return (if b then (x # ys) else ys) od."
}
context:{
    "name":"(Code)State Selection with Relation: Select a new state based on a given relation, ensuring that the set of possible new states is non-empty before making the selection."
}
context:{
    "name": "(Both)Exception Handling: Define `throwError` to set the failure flag and return an empty set of results, and `catch` to handle exceptions by providing a fallback computation if an exception is thrown. Ensure that `catch` checks the failure flag and applies the handler function if necessary."
}
context:{
    "name": "(Both)Exception Handling: Define `throwError` to set the failure flag and return an empty set of results, and `catch` to handle exceptions by providing a fallback computation if an exception is thrown. Ensure that `catch` checks the failure flag and applies the handler function if necessary."
}
context:{
    "name":"(Both)Exception Handling: Define `throwError` to set the failure flag and return an empty set of results, and `catch` to handle exceptions by providing a fallback computation if an exception is thrown. Ensure that `catch` checks the failure flag and applies the handler function if necessary."
}
context:{
    "name": "(Both)Exception Handling: Define `throwError` to set the failure flag and return an empty set of results, and `catch` to handle exceptions by providing a fallback computation if an exception is thrown. Ensure that `catch` checks the failure flag and applies the handler function if necessary."
}
context:{
    "name": "(Code)Loop Execution with Exception Handling: The while loop executes as long as the condition is true, and it handles non-termination and exceptions using a nondeterministic monad. The loop terminates if the condition is false or if all possible next states lead to termination. If the loop fails to terminate, it returns a failure flag."
}
context:{
    "name": "(Code)Control Flow with Conditions: Provides combinators for conditional and repetitive execution within a nondeterministic state monad, enabling the evaluation of conditions with side effects and the execution of corresponding actions. These combinators include negation, while loops, if-then-else statements, and logical operations, allowing for flexible and expressive control flow in the presence of nondeterminism."
}"""

In [26]:
from openai import OpenAI

key = ['sk-a6c628b29e2f4b65b0ecd322f21e669f','sk-f4ebc969b87e41d7bf1dc91dd5026bba','sk-0fc3a02ca767436d91bea234f2f9d4e7','sk-de00e7083c4542458bfdcdc8158374a7','sk-68921001062244bd9d71139b015d1b9c']
client = OpenAI(
    # 若没有配置环境变量，请用API Key将下行替换为：api_key="sk-xxx",
    api_key = 'sk-68921001062244bd9d71139b015d1b9c',
    base_url="https://dashscope.aliyuncs.com/compatible-mode/v1",
)

# 创建一个空字符串来累积来自各chunk的内容
full_reply_content = ""

completion = client.chat.completions.create(
    model="llama3.1-405b-instruct",
    messages=[
        {'role': 'system', 'content': 'You are a helpful assistant.'},
        {'role': 'user', 'content': "你好"}
    ],
    stream=True
)

for chunk in completion:
    # 检查并累积chunk中的增量内容
    delta = chunk.choices[0].delta
    if hasattr(delta, 'content') and delta.content is not None:
        full_reply_content += delta.content  # 累积内容到完整回答中
        print(delta.content, end='', flush=True)  # 实时显示增量内容给用户

print("\n\n完整回答: " + full_reply_content)

RateLimitError: Error code: 429 - {'error': {'message': 'You exceeded your current requests list.', 'type': 'limit_requests', 'param': None, 'code': 'limit_requests'}, 'request_id': 'a957fef9-7473-9d3e-9df4-e43f5132c584'}

In [6]:
from langchain.prompts import PromptTemplate
from langchain.memory import ConversationBufferWindowMemory
from langchain_community.chat_models import ChatOllama
from langchain.chains import ConversationChain, LLMChain
import json
import time

def formalize_specifications(context_list, json_tree, llm, json_llm):
    # 定义提示模板
    reduce_duplicates_prompt = '''
    Please eliminate any duplicates specifications from the following Specification Tree, which is a hierarchical structure where the leaf nodes represent individual specifications and the root node represents the overarching topic. 
Please note:
i.Only delete specification when the semantics are exactly the same.
ii.Only determine specification repeatability between the same level under the same mother node.
iii.Don't change the highest level of the Specification Tree.
(Code) or (Both) tag: 
i.if you merge a (Code)/(Both) and No tag specification, reserve (Code)/(Both).
ii.if you merge a (Code) and (Both) specification, reserve (Both).
Your response should strictly follow the json format of the provided Specification Tree (each specification is in the "Name:Description" format), and response only with the updated Specification Tree, no additional explanation or statement.
    {specification}
[Updated Specification Tree]:
    '''

    identify_purpose_prompt = '''
Please summarize the following specifications into one specification(named [code-spec]) of json format.
[code-spec] example 1:
{{
  "name": "Underspecification of Behaviour: The model leaves as much behaviour as possible underspecified, making fewer assumptions about the hardware."
}}
[code-spec] example 2:
{{
  "name": "Restriction of Side Effects: Functions in the machine interface are restricted to only affect the machine_state component of the system."
}}
Note that only learn format from the examples, don't use their information to summarize specification. Each [code-spec] should have a name and an explanation, combined as "name:explanation". Your answer should be a JSON with a single key "name" and a value of the [code-spec] in the format of "name:explanation".
Specifications should be summarized to one specification([code-spec]):
{code}
'''
    
    identify_implemented_spec_prompt = '''
Please review the following [Specification Tree] and determine if the [code-spec] is already included in the tree. 
- If the [code-spec] is similar to any specification(refered as [pecifiaction A]) in the [Specification Tree], please reply with and only with the following json format, no additional explanation or statement:
{{
    "name":"(Both)[pecifiaction A]"
}}
- If the specification is not similar to any specification, please reply with and only with the following json format:
{{
    "name":"(Code)content of [code-spec]"
}}
[Specification Tree]:
{specification}
    '''
    
    update_spec_tree_prompt = '''
    [Origin Specification Tree] maintains a tree structure among specifications, with nodes at the same depth having similar granularity. 
    Please update the [Origin Specification Tree] according to the [contexts].
    if specification A in the [contexts] starts with (Code), adding "(Code)specification A" to the [Origin Specification Tree] in appropriate level.
    if specification A in the [contexts] starts with (Both), adding (Both) to the corresponding specification in the [Origin Specification Tree].
    Respond only with the final updated [Origin Specification Tree] in json format, with no additional commentary. Don't change the highest level of the [Origin Specification Tree].
    Make sure that your answer follows the following format, contains "name" and "children" 2 keys: 
{{
  "name": "",
  "children": [
    {{
      "name": "",
      "children": []
    }},
    {{
      "name": "",
      "children": []
    }}
  ]
}}
    [Origin Specification Tree]:
    {specification}
    [contexts]:
    {context}
    '''
    
    # 初始化语言模型
    # llm = ChatOllama(model='llama3.1:70b', temperature=0,num_ctx=12288)
    # json_llm = ChatOllama(model='llama3.1:70b', temperature=0,format='json',num_ctx=12288)
    
    

    useful_context = ""
    
    for context in context_list:
        # 创建记忆存储，限制为 2 轮对话
        memory = ConversationBufferWindowMemory(k=2)
        
        # 初始化对话链
        conversation = ConversationChain(
            llm=llm,
            memory=memory,
            verbose=True
        )

        # Step 1: 识别Isabelle代码的目的和意图
        prompt_purpose = PromptTemplate(input_variables=["code"], template=identify_purpose_prompt)
        purpose_response = conversation.predict(input=prompt_purpose.format(code=context))
        print("Purpose Response:", purpose_response)
        time.sleep(15)

        # Step 2: 使用减少重复后的规约树识别已实现的规约
        prompt_identify_spec = PromptTemplate(input_variables=["specification"], template=identify_implemented_spec_prompt)
        implemented_spec_response = conversation.predict(input=prompt_identify_spec.format(specification=json_tree))
        print("Implemented Specifications Response:", implemented_spec_response)
        useful_context += f"context:{implemented_spec_response}\n"
        time.sleep(15)
      
    # Step 3: 更新规约树
    update_spec_tree_str = update_spec_tree_prompt.format(specification=json_tree, context=useful_context)
    from openai import OpenAI

    client = OpenAI(
        # 若没有配置环境变量，请用API Key将下行替换为：api_key="sk-xxx",
        api_key = 'sk-a6c628b29e2f4b65b0ecd322f21e669f',
        base_url="https://dashscope.aliyuncs.com/compatible-mode/v1",
    )
    full_reply_content = ""

    completion = client.chat.completions.create(
        model="llama3.1-405b-instruct",
        messages=[
            {'role': 'user', 'content': update_spec_tree_str}
        ],
        stream=True
    )

    for chunk in completion:
        # 检查并累积chunk中的增量内容
        delta = chunk.choices[0].delta
        if hasattr(delta, 'content') and delta.content is not None:
            full_reply_content += delta.content  # 累积内容到完整回答中
            print(delta.content, end='', flush=True)  # 实时显示增量内容给用户

    updated_spec_tree_response = full_reply_content.strip()
       
    # Step 4: 减少规约树的重复性
    reduce_duplicates_chain = LLMChain(
        llm=json_llm, 
        prompt=PromptTemplate(input_variables=["specification"], template=reduce_duplicates_prompt)
    )
    try:
        spec_tree_response = reduce_duplicates_chain.run(specification=updated_spec_tree_response)
    except Exception:
        with open('log.txt','a') as f:
            f.write(update_spec_tree_prompt.format(specification=json_tree, context=useful_context))
    print("Reduced Specification Tree:", spec_tree_response)
    
    return spec_tree_response


In [24]:
def escape_double_quotes(s):
    # 标记是否在转义状态
    in_escape = False
    # 存储结果的字符串
    result = ""

    # 遍历字符串中的每个字符
    for char in s:
        if char == '\\':
            # 如果当前是转义状态，则添加转义字符到结果中，并退出转义状态
            result += char
            in_escape = True
        elif char == '"':
            # 如果字符是引号且不在转义状态，则替换为转义的引号
            if not in_escape:
                result += '\\"'
            else:
                result += char
            in_escape = False
        else:
            # 其他情况下，直接添加字符到结果中
            result += char
            in_escape = False

    return result

# 测试函数
test_string = 'He said, \"Hello, world!" and then left.'
escaped_string = escape_double_quotes(test_string)
print(escaped_string)

He said, \"Hello, world!\" and then left.


In [9]:
related_nodes[6:]

['Threads and TCBs',
 'Scheduler',
 'Toplevel ARM Definitions',
 'CSpace',
 'Prefix order on lists as order class instance',
 'IPC Cancelling',
 'ARM VSpace Functions',
 'Retyping and Untyped Invocations',
 'Kernel Object Invocations',
 'ARM Object Invocations',
 'Accessing the ARM VSpace',
 'Accessing CSpace',
 'Accessing the Kernel Heap',
 'Basic Kernel and Exception Monads',
 'Abstract Specification Instantiations',
 'Basic Data Structures',
 'Machine Operations',
 'ARM-Specific Data Types',
 'ARM-Specific Virtual-Memory Rights',
 'Access Rights',
 'Error and Fault Messages',
 'Machine Accessor Functions',
 'ARM Machine Instantiation',
 'Common, Architecture-Specific Data Types',
 'Kernel Events',
 'Machine Types',
 'ARM Machine Types',
 'Platform Definitions',
 'Machine Word Setup',
 'Enumeration instances for Words',
 'Enumerations',
 'Nondeterministic State Monad with Failure']

In [10]:
import os
import json
from neo4j import GraphDatabase
import glob

# Neo4j数据库连接信息
NEO4J_URI = os.getenv("NEO4J_URI", "bolt://localhost:7687")
NEO4J_USERNAME = os.getenv("NEO4J_USERNAME", "neo4j")
NEO4J_PASSWORD = os.getenv("NEO4J_PASSWORD", "neo4jneo4j")

# 创建数据库驱动
driver = GraphDatabase.driver(NEO4J_URI, auth=(NEO4J_USERNAME, NEO4J_PASSWORD))

def get_tree(tx, root_node_name):
    query = """
    MATCH (n {name: $root_node_name})
    OPTIONAL MATCH (n)-[:SPECIFY]->(child)
    RETURN n.name AS name, collect(child.name) AS children
    """
    result = tx.run(query, root_node_name=root_node_name)
    record = result.single()
    if record:
        name = record["name"]
        children_names = [child for child in record["children"] if child is not None]
        children = []
        for child_name in children_names:
            child_tree = get_tree(tx, child_name)  # 递归获取子节点
            children.append(child_tree)
        return {"name": name, "children": children}
    else:
        return {"name": root_node_name, "children": []}  # 如果没有找到节点，返回空的子节点列表

def get_and_display_tree(root_node_name):
    with driver.session() as session:
        tree = session.read_transaction(get_tree, root_node_name)
        json_tree = json.dumps(tree, indent=2, ensure_ascii=False)
        return json_tree

def delete_children(tx, node_name):
    # 递归删除所有子节点
    query = """
    MATCH (parent:Query {name: $node_name})-[:SPECIFY]->(child)
    RETURN child
    """
    result = tx.run(query,node_name=node_name)
    children = [record["child"] for record in result]
    
    for child in children:
        child_name = child['name']
        #child_name = escape_double_quotes(child_name)
        # 删除子节点
        delete_children(tx, child_name)  # 递归删除子节点
        tx.run("MATCH (n:Query {name: $name}) DETACH DELETE n", name=child_name)

def delete_all_children_except_node(node_name):
    with driver.session() as session:
        session.write_transaction(delete_children, node_name)

def insert_tree(tx, tree, parent=None):
    node_name = tree["name"] 
    
    # 创建节点
    query = "MERGE (n:Query {name: $name})"
    tx.run(query, name=node_name)
    
    # 如果有父节点，创建关系
    if parent:
        relation_query = """
        MATCH (parent:Query {name: $parent_name}), (child:Query {name: $child_name})
        CREATE (parent)-[:SPECIFY]->(child)
        """
        tx.run(relation_query, parent_name=parent, child_name=node_name)

    # 递归插入
    for child in tree.get("children", []):
        insert_tree(tx, child, node_name)

def insert_updated_spec_tree(updated_spec_tree_response):
    # 将响应转换为 JSON 格式
    tree = json.loads(updated_spec_tree_response)
    
    with driver.session() as session:
        session.write_transaction(insert_tree, tree)
    
import json
import os

def get_codes_by_node(node):
    relation = {
    "Platform Definitions": "./spec/machine/ARM/Platform.thy",
    "ARM Machine Types": "./spec/design/m-skel/ARM/MachineTypes.thy",
    "Machine Types": "./spec/design/m-skel/ARM/MachineTypes.thy",
    "Kernel Events": "./spec/design/skel/Event_H.thy",
    "Common, Architecture-Specific Data Types": "./spec/design/skel/ARM/Arch_Structs_B.thy",
    "ARM Machine Instantiation": "./spec/abstract/ARM/Machine_A.thy",
    "Machine Accessor Functions": "./spec/abstract/MiscMachine_A.thy",
    "Error and Fault Messages": "./spec/abstract/ExceptionTypes_A.thy",
    "Access Rights": "./spec/abstract/CapRights_A.thy",
    "ARM-Specific Virtual-Memory Rights": "./spec/abstract/VMRights_A.thy",
    "ARM-Specific Data Types": "./spec/abstract/ARM/Arch_Structs_A.thy",
    "Machine Operations": "./spec/machine/ARM/MachineOps.thy",
    "Basic Data Structures": "./spec/abstract/Structures_A.thy",
    "Abstract Specification Instantiations": "./spec/abstract/Deterministic_A.thy",
    "Basic Kernel and Exception Monads": "./spec/abstract/Exceptions_A.thy",
    "Accessing the Kernel Heap": "./spec/abstract/KHeap_A.thy",
    "Accessing CSpace": "./spec/abstract/CSpaceAcc_A.thy",
    "Accessing the ARM VSpace": "./spec/abstract/ARM/ArchVSpaceAcc_A.thy",
    "ARM Object Invocations": "./spec/abstract/ARM/ArchInvocation_A.thy",
    "Kernel Object Invocations": "./spec/abstract/InvocationLabels_A.thy",
    "Retyping and Untyped Invocations": "./spec/abstract/Retype_A.thy",
    "ARM VSpace Functions": "./spec/abstract/ARM/ArchVSpace_A.thy",
    "IPC Cancelling": "./spec/abstract/IpcCancel_A.thy",
    "CSpace": "./spec/abstract/CSpace_A.thy",
    "Toplevel ARM Definitions": "./spec/abstract/ARM/Arch_A.thy",
    "Scheduler": "./spec/abstract/Schedule_A.thy",
    "Threads and TCBs": "./spec/abstract/Tcb_A.thy",
    "IPC": "./spec/sep-abstract/Ipc_SA.thy",
    "Interrupts": "./spec/abstract/Interrupt_A.thy",
    "Kernel Invocation Labels": "./spec/design/skel/InvocationLabels_H.thy",
    "Decoding System Calls": "./spec/abstract/Decode_A.thy",
    "An Initial Kernel State": "./spec/abstract/ARM/Init_A.thy",
    "System Calls": "./spec/abstract/Syscall_A.thy",
    "Nondeterministic State Monad with Failure":"./spec/abstract/Nondeterministic State Monad with Failure.thy"
    }
    with open("../PropertyExtract/output-qwen-max.jsonl", "r", encoding="utf-8") as f:
        code_list = []
        for line in f:
            data = json.loads(line)
            if data['title'] == relation.get(node,''):
                code_list.append({f"property:{data['property']}"})
        return code_list

In [12]:
from langchain_openai import ChatOpenAI
os.environ["OPENAI_API_KEY"]='sk-c1bb7b06f7434e2aa6871f22f088cd78'
llm = ChatOpenAI(
    model="qwen-max",
    temperature=0,
    max_tokens=None,
    timeout=300,
    max_retries=2,
    base_url="https://dashscope.aliyuncs.com/compatible-mode/v1"
)

In [11]:
from langchain_openai import ChatOpenAI
json_llm = ChatOllama(model='llama3.1:70b', temperature=0, format='json',num_ctx=12288)
i = 0
for node in related_nodes[7:]:
    key = ['sk-f4ebc969b87e41d7bf1dc91dd5026bba','sk-0fc3a02ca767436d91bea234f2f9d4e7','sk-de00e7083c4542458bfdcdc8158374a7']
    os.environ["OPENAI_API_KEY"]=key[i%3]
    llm = ChatOpenAI(
        model="llama3.1-405b-instruct",
        temperature=0,
        max_tokens=None,
        timeout=300,
        max_retries=2,
        base_url="https://dashscope.aliyuncs.com/compatible-mode/v1"
    )
    # os.environ["OPENAI_API_KEY"]='sk-c1bb7b06f7434e2aa6871f22f088cd78'
    # llm = ChatOpenAI(
    #     model="qwen-max",
    #     temperature=0,
    #     max_tokens=None,
    #     timeout=300,
    #     max_retries=2,
    #     base_url="https://dashscope.aliyuncs.com/compatible-mode/v1"
    # )
    codes = get_codes_by_node(node)
    if len(codes)==0:
        print(f"pass {node}")
        continue
    json_tree = get_and_display_tree(node)
    result = formalize_specifications(codes, json_tree, llm, json_llm)
    with open(f'./polish/llama405b/{node}.txt','a') as output:
        output.write(result)
    delete_all_children_except_node(node)
    insert_updated_spec_tree(result)
    i += 1

/tmp/ipykernel_2071684/244431213.py:35: DeprecationWarning: read_transaction has been renamed to execute_read
  tree = session.read_transaction(get_tree, root_node_name)




> Entering new ConversationChain chain...
Prompt after formatting:
The following is a friendly conversation between a human and an AI. The AI is talkative and provides lots of specific details from its context. If the AI does not know the answer to a question, it truthfully says it does not know.

Current conversation:

Human: 
Please summarize the following specifications into one specification(named [code-spec]) of json format.
[code-spec] example 1:
{
  "name": "Underspecification of Behaviour: The model leaves as much behaviour as possible underspecified, making fewer assumptions about the hardware."
}
[code-spec] example 2:
{
  "name": "Restriction of Side Effects: Functions in the machine interface are restricted to only affect the machine_state component of the system."
}
Note that only learn format from the examples, don't use their information to summarize specification. Each [code-spec] should have a name and an explanation, combined as "name:explanation". Your answer shoul

/home/zhuxy/anaconda3/envs/OSAF/lib/python3.9/site-packages/langchain_core/_api/deprecation.py:119: LangChainDeprecationWarning: The class `LLMChain` was deprecated in LangChain 0.1.17 and will be removed in 0.3.0. Use RunnableSequence, e.g., `prompt | llm` instead.
  warn_deprecated(
/home/zhuxy/anaconda3/envs/OSAF/lib/python3.9/site-packages/langchain_core/_api/deprecation.py:119: LangChainDeprecationWarning: The method `Chain.run` was deprecated in langchain 0.1.0 and will be removed in 0.3.0. Use invoke instead.
  warn_deprecated(


Reduced Specification Tree: {
  "name": "Scheduler",
  "children": [
    {
      "name": "Thread Activation: A thread can only be activated if it is not already running.",
      "children": []
    },
    {
      "name": "Scheduling Context Binding: A scheduling context can only be bound to one thread at a time.",
      "children": []
    },
    {
      "name": "(Both)Thread State: A thread's state can only be set to a valid state (e.g., Runnable, Idle, etc.).",
      "children": []
    },
    {
      "name": "Maximum Controlled Priority: A thread can only set priorities and MCPs to be less than or equal to the provided thread's MCP.",
      "children": []
    },
    {
      "name": "Yield To: If a thread yields to another thread with the same priority, the yielded thread will be scheduled next and placed at the head of the scheduling queue.",
      "children": []
    },
    {
      "name": "(Both)Thread Scheduling: The highest priority thread in a runnable state is chosen for schedulin

/tmp/ipykernel_2071684/244431213.py:57: DeprecationWarning: write_transaction has been renamed to execute_write
  session.write_transaction(delete_children, node_name)
/tmp/ipykernel_2071684/244431213.py:83: DeprecationWarning: write_transaction has been renamed to execute_write
  session.write_transaction(insert_tree, tree)
/tmp/ipykernel_2071684/244431213.py:35: DeprecationWarning: read_transaction has been renamed to execute_read
  tree = session.read_transaction(get_tree, root_node_name)


...

/tmp/ipykernel_2071684/244431213.py:57: DeprecationWarning: write_transaction has been renamed to execute_write
  session.write_transaction(delete_children, node_name)
/tmp/ipykernel_2071684/244431213.py:83: DeprecationWarning: write_transaction has been renamed to execute_write
  session.write_transaction(insert_tree, tree)


pass Enumeration instances for Words
pass Enumerations


/tmp/ipykernel_2071684/244431213.py:35: DeprecationWarning: read_transaction has been renamed to execute_read
  tree = session.read_transaction(get_tree, root_node_name)




> Entering new ConversationChain chain...
Prompt after formatting:
The following is a friendly conversation between a human and an AI. The AI is talkative and provides lots of specific details from its context. If the AI does not know the answer to a question, it truthfully says it does not know.

Current conversation:

Human: 
Please summarize the following specifications into one specification(named [code-spec]) of json format.
[code-spec] example 1:
{
  "name": "Underspecification of Behaviour: The model leaves as much behaviour as possible underspecified, making fewer assumptions about the hardware."
}
[code-spec] example 2:
{
  "name": "Restriction of Side Effects: Functions in the machine interface are restricted to only affect the machine_state component of the system."
}
Note that only learn format from the examples, don't use their information to summarize specification. Each [code-spec] should have a name and an explanation, combined as "name:explanation". Your answer shoul

/tmp/ipykernel_2071684/244431213.py:57: DeprecationWarning: write_transaction has been renamed to execute_write
  session.write_transaction(delete_children, node_name)
/tmp/ipykernel_2071684/244431213.py:83: DeprecationWarning: write_transaction has been renamed to execute_write
  session.write_transaction(insert_tree, tree)


In [20]:
# 切换到qwen-70b的图谱
for node in related_nodes:
    with open(f'./polish/llama31-70b/{node}.txt','a') as f:
        f.write(get_and_display_tree(node))

/tmp/ipykernel_2420460/1918806020.py:35: DeprecationWarning: read_transaction has been renamed to execute_read
  tree = session.read_transaction(get_tree, root_node_name)
